In [6]:
import os
train_qrel_file = './train.qrel'
test_qrel_file = './test.qrel'
sorted_bm25_file = './Query_extract/bm25_full_turn_2'
train_output_file = './Query_extract/train_before_overlap2_full_turn'
test_output_file = './Query_extract/test_before_overlap2_full_turn'
# Function to extract facet_ids (Fnnnn) from a qrel file
def extract_facet_ids(qrel_file):
    with open(qrel_file, 'r') as f:
        lines = f.readlines()
        print(f"Lines from {qrel_file}: {lines}")  # For debugging purposes
    # Extract the second column (facet_id), assuming a consistent format
    facet_ids = {line.split()[0] for line in lines if len(line.split()) > 1}  # Handle any malformed lines
    return facet_ids

# Extract facet_ids from train.qrel and test.qrel
train_facet_ids = extract_facet_ids(train_qrel_file)
test_facet_ids = extract_facet_ids(test_qrel_file)

# Read the sorted BM25 file
with open(sorted_bm25_file, 'r') as f:
    sorted_lines = f.readlines()

# Function to filter lines by facet_id
def filter_by_facet_ids(facet_ids, lines):
    filtered_lines = []
    for line in lines:
        # Make sure the line is properly split and has enough components
        parts = line.split()
        if len(parts) > 1 and parts[1] in facet_ids:
            filtered_lines.append(line)
    return filtered_lines

# Find the overlap for train and test
train_overlap = filter_by_facet_ids(train_facet_ids, sorted_lines)
test_overlap = filter_by_facet_ids(test_facet_ids, sorted_lines)

# Save the results for train overlaps
with open(train_output_file, 'w') as f:
    f.writelines(train_overlap)

# Save the results for test overlaps
with open(test_output_file, 'w') as f:
    f.writelines(test_overlap)

print(f"Train BM25 overlap saved to {train_output_file}")
print(f"Test BM25 overlap saved to {test_output_file}")


Lines from ./train.qrel: ['F0001 0 clueweb09-en0038-74-08250 1\n', 'F0001 0 clueweb09-enwp01-17-11113 1\n', 'F0002 0 clueweb09-en0001-02-21241 1\n', 'F0002 0 clueweb09-en0006-52-11056 1\n', 'F0002 0 clueweb09-en0009-48-37458 1\n', 'F0002 0 clueweb09-en0010-27-33585 1\n', 'F0002 0 clueweb09-en0020-29-24783 1\n', 'F0002 0 clueweb09-en0024-15-26205 1\n', 'F0002 0 clueweb09-en0024-52-20047 1\n', 'F0002 0 clueweb09-en0025-09-34197 1\n', 'F0002 0 clueweb09-en0025-89-06994 1\n', 'F0002 0 clueweb09-en0038-74-08247 1\n', 'F0002 0 clueweb09-en0038-74-08251 1\n', 'F0002 0 clueweb09-en0043-86-05608 1\n', 'F0002 0 clueweb09-en0048-08-23614 1\n', 'F0002 0 clueweb09-en0053-22-05225 1\n', 'F0002 0 clueweb09-en0080-93-13806 1\n', 'F0002 0 clueweb09-en0101-64-04019 1\n', 'F0002 0 clueweb09-en0104-24-18374 1\n', 'F0002 0 clueweb09-en0107-80-01451 1\n', 'F0002 0 clueweb09-en0121-78-15657 1\n', 'F0002 0 clueweb09-en0122-51-07029 1\n', 'F0002 0 clueweb09-enwp00-00-09498 1\n', 'F0002 0 clueweb09-enwp00-02-18

In [18]:
# Define the input and output file names
input_file = './Query_extract/test_before_overlap2_full_turn'  # Replace with your actual file name
output_file = './Query_extract/test_before_overlap2_clean_full_turn'

# Open the input file for reading and the output file for writing
with open(input_file, 'r') as infile, open(output_file, 'w') as outfile:
    for line in infile:
        # Remove the 'bm25' suffix and write the cleaned line to the output file
        cleaned_line = line.replace('bm25', '').strip()  # Remove 'bm25' and any trailing whitespace
        outfile.write(cleaned_line + '\n')

print("Cleaning complete! Check 'cleaned_data.txt' for the results.")

Cleaning complete! Check 'cleaned_data.txt' for the results.


In [7]:
import pandas as pd

# Load the CSV file
input_file = "./newfiles/intent_results_3_full.csv"  # Change this to your actual file name
output_file = "./newfiles/intent_results_3_full.csv"  # Change this to your desired output file name

# Read the CSV file
df = pd.read_csv(input_file)

# Add an ID column
df.insert(0, "id", range(len(df)))

# Save the updated CSV
df.to_csv(output_file, index=False)

print(f"Updated CSV saved as {output_file}")


Updated CSV saved as ./newfiles/intent_results_3_full.csv


In [26]:
import json
import csv
#This is the file for ground-truth training/testing/validation qrels 
train_file = './Query_extract/test_before_overlap2_clean_first_turn'
qrels = './test.qrel'
# facets = '/home/yyuan/MQC/facet_data/faceted_all_records.csv'
#This is the file that stores all the data including image & qa pairs & topics
facets = './newfiles/intent_results_2_first.csv'
trains =  open(train_file,'r').readlines()
qrels = open(qrels,'r').readlines()
# facet_id = [t.split(' ')[0] for t in trains]
doc_dict = {}
qrels_dict = {}
facet_doc_score = {}
facets = list(csv.DictReader(open(facets)))
facet_topic = {f['id']: f['topic'] for f in facets}
facet_topicid = {f['id']: f['topic_id'] for f in facets}


facet_query = {f['id']:f['query'] for f in facets}
facet_id = {f['id']:f['facet_id'] for f in facets}
facet_img1 = {}
import pickle
# img_features = pickle.load(open('/ivi/ilps/personal/yyuan/img_feature_all.pkl','rb'))
for f in facets:
    facet_img1[f['id']] = []
    for i in range(1,4):
        # if f[f'image{i}'] in img_features:
        facet_img1[f['id']].append(f[f'image1_{i}'])


facet_img2 = {}
for f in facets:
    facet_img2[f['id']] = []
    for i in range(1,4):
        # if f[f'image{i}'] in img_features:
        facet_img2[f['id']].append(f[f'image2_{i}'])


# facet_img3 = {}
# for f in facets:
#     facet_img3[f['id']] = []
#     for i in range(1,4):
#         # if f[f'image{i}'] in img_features:
#         facet_img3[f['id']].append(f[f'image3_{i}'])

# facet_img4 = {}
# for f in facets:
#     facet_img4[f['id']] = []
#     for i in range(1,4):
#         # if f[f'image{i}'] in img_features:
#         facet_img4[f['id']].append(f[f'image4_{i}'])

for t in trains:
    facet_id = t.split(' ')[1]
    doc_id = t.split(' ')[3]
    id=t.split(' ')[0]
    if (id,facet_id) not in doc_dict:
        doc_dict[(id, facet_id)] = []
    doc_dict[(id, facet_id)].append(doc_id)   
    # doc_dict[facet_id].append(doc_id)
    facet_doc_score[(id,facet_id,doc_id)] = t.strip('\n').split(' ')

qrels_dict = {}
for q in qrels:
    facet_id = q.split(' ')[0]
    doc_id = q.split(' ')[2]
    relevance_score = int(q.split(' ')[-1])

    if facet_id not in qrels_dict:
        qrels_dict[facet_id] = []

    if relevance_score > 0:  # Only include relevant documents
        qrels_dict[facet_id].append(doc_id)

# Build overlap_dict and limit it to the top 5 relevant documents
overlap_dict = {}
for (id, facet) in doc_dict:
    # Take the intersection of doc_dict[(id, facet)] and qrels_dict
    if facet in qrels_dict:
        overlap_docs = [
            doc for doc in doc_dict[(id, facet)] if doc in qrels_dict[facet]
        ]
    else:
        overlap_docs = []

    # Sort the overlap_docs by relevance score and limit to the top 5
    overlap_dict[(id, facet)] = sorted(
        overlap_docs,
        key=lambda x: facet_doc_score[(id, facet, x)],
        reverse=True
    )[:5]  # Keep only the top 5

l = [d for d in overlap_dict if len(overlap_dict[d])>0]

all_records = []
for k,(id,facet) in enumerate(doc_dict):
    record = {}
    record['facet_id'] = facet
    record['related_dict'] = doc_dict[(id,facet)]
    record['topic_id'] = facet_topicid[id]
    record['topic'] = facet_topic[id]
    record['question1'] = facet_query[id]
    record['img_ids1'] = facet_img1[id]
    record['img_ids2'] = facet_img2[id]
    # record['img_ids3'] = facet_img3[id]
    # record['img_ids4'] = facet_img4[id]

    if len(doc_dict[(id,facet)])>0:
        all_records.append(record)
print(len(all_records))
with open('./Query_extract/First_turn_query/test_after_overlap2_first_turn_poop.json','w') as f:
    json.dump(all_records,f)

778


In [2]:
import json

In [28]:
json_file1 = './Query_extract/First_turn_query/test_after_overlap2_first_turn_poop.json'
json_file2 = './Query_extract/First_turn_query/test_after_overlap3_first_turn_poop.json'
json_file3 = './Query_extract/First_turn_query/test_after_overlap4_first_turn_poop.json'

# Load the JSON files
with  open(json_file2, 'r') as f2, open(json_file3, 'r') as f3, open(json_file1, 'r') as f1:
    data1 = json.load(f1)  # List of dictionaries
    data2 = json.load(f2)  # List of dictionaries
    data3 = json.load(f3)  # List of dictionaries

# Combine the lists of dictionaries (just concatenating lists)
combined_data =   data1 + data2 + data3

# Save the combined data into a new file
with open('./Query_extract/First_turn_query/test_dataset_bert_first_turn_poop.json', 'w') as f_out:
    json.dump(combined_data, f_out, indent=4)

print("Combined JSON saved to 'combined_data_test.json'")

Combined JSON saved to 'combined_data_test.json'


In [58]:
json_file1 = './devtrain_2turn_new.json'
json_file2 = './devtrain_3turn_new.json'
json_file3 = './devtrain_4turn_new.json'

# Load the JSON files
with open(json_file1, 'r') as f1, open(json_file2, 'r') as f2, open(json_file3, 'r') as f3:
    data1 = json.load(f1)  # List of dictionaries
    data2 = json.load(f2)  # List of dictionaries
    data3 = json.load(f3)  # List of dictionaries

# Combine the lists of dictionaries (just concatenating lists)
combined_data = data1 + data2 + data3

# Save the combined data into a new file
with open('combined_data_train.json', 'w') as f_out:
    json.dump(combined_data, f_out, indent=4)


In [5]:
import json

def combine_json_files(file1, file2, output_file):
    # Load the first JSON file
    with open(file1, 'r') as f1:
        data1 = json.load(f1)

    # Load the second JSON file
    with open(file2, 'r') as f2:
        data2 = json.load(f2)

    # Combine the data assuming they are lists

    combined_data = data1 + data2
    

    # Write the combined data to a new JSON file
    with open(output_file, 'w') as out_file:
        json.dump(combined_data, out_file, indent=4)

# Example usage
combine_json_files('../datasets/train_dataset_bert.json', '../datasets/test_dataset_bert.json', '../datasets/all.json')

In [71]:
# Input and output file names
import json
input_file = './first_turn/train_dataset_bert_first_turn.json'  # Change this to your actual filename
output_file = './first_turn/train_first_turn.pairs'

# Open the output file for writing
with open(output_file, 'w') as out_file:
    # Read the entire .json file
    with open(input_file, 'r') as in_file:
        data = json.load(in_file)  # Load the JSON data
        
        # Process each entry in the JSON data
        for entry in data:
            facet_id = entry['facet_id'][1:]  # Remove the 'F'
            related_ids = entry['related_dict']
            
            # Write each related_id as a pair with the facet_id
            for related_id in related_ids:
                out_file.write(f"{facet_id} {related_id}\n")

print(f"Pairs written to {output_file}")

Pairs written to ./first_turn/train_first_turn.pairs


In [74]:
# Input and output file names
import json
input_file = './first_turn/train_dataset_bert_first_turn.json'  # Change this to your actual filename
output_file = './first_turn/queries_train_first_turn.tsv'

# Open the output file for writing
with open(output_file, 'w') as out_file:
    # Write the header
    
    # Read the entire .json file
    with open(input_file, 'r') as in_file:
        data = json.load(in_file)  # Load the JSON data
        
        # Process each entry in the JSON data
        for entry in data:
            topic = 'query'
            facet_id = entry['facet_id'][1:]  # Remove the 'F'
            
            # Constructing the conversation history
            conversation_history = []
            for i in range(1, 5):  # Assuming maximum 4 pairs (question/answer)
                question_key = f'question{i}'
                answer_key = f'answer{i}'
                
                if question_key in entry and answer_key in entry:
                    conversation_history.append(f"Gpt: {entry[question_key]} USER: {entry[answer_key]}")
            
            # Join the conversation history into a single string
            conversation_str = " ".join(conversation_history)
            
            # Write the data as a tab-separated line
            out_file.write(f"{topic}\t{facet_id}\t{conversation_str}\n")

print(f"Conversations written to {output_file}")

Conversations written to ./first_turn/queries_train_first_turn.tsv


In [75]:
# Input and output file names
file1 = './first_turn/queries_train_first_turn.tsv'  # Change this to your first TSV filename
file2 = './first_turn/queries_test_first_turn.tsv'  # Change this to your second TSV filename
output_file = './first_turn/combined_queries_first_turn.tsv'  # Name of the output file

# Open the output file for writing
with open(output_file, 'w') as out_file:
    # Read the first TSV file and write its content
    with open(file1, 'r') as in_file1:
        for line in in_file1:
            out_file.write(line)
    
    # Read the second TSV file and write its content
    with open(file2, 'r') as in_file2:
        for line in in_file2:
            out_file.write(line)

print(f"Combined TSV written to {output_file}")

Combined TSV written to ./first_turn/combined_queries_first_turn.tsv


In [76]:
# Input and output file names
file1 = './first_turn/test_before_overlap2_first_turn'  # Change this to your first TSV filename
file2 = './first_turn/test_before_overlap3_first_turn'
file3 = './first_turn/test_before_overlap4_first_turn'
output_file = './first_turn/combined_test_first_turn.run'  # Name of the output file

# Open the output file for writing
with open(output_file, 'w') as out_file:
    # Read the first TSV file and write its content
    with open(file1, 'r') as in_file1:
        for line in in_file1:
            out_file.write(line)
    
    # Read the second TSV file and write its content
    with open(file2, 'r') as in_file2:
        for line in in_file2:
            out_file.write(line)
        # Read the second TSV file and write its content
    with open(file3, 'r') as in_file2:
        for line in in_file2:
            out_file.write(line)

print(f"Combined TSV written to {output_file}")

Combined TSV written to ./first_turn/combined_test_first_turn.run


In [77]:
# Input and output file names
input_file = './first_turn/combined_test_first_turn.run'  # Change this to your actual input filename
output_file = './first_turn/test_first_turn.run'  # Desired output filename

# Open the output file for writing
with open(output_file, 'w') as out_file:
    # Read the input .run file
    with open(input_file, 'r') as in_file:
        for line in in_file:
            # Split the line into parts
            parts = line.split()
            if len(parts) >= 7:
                # Extract the relevant pieces
                facet_id = parts[1][1:]  # Remove the 'F' from the facet_id
                query_id = 'Q0'  # Static value as per your format
                doc_id = parts[3]
                rank = parts[4]
                score_with_method = parts[6]  # This contains the score and method
                
                # Separate score and method
                score = score_with_method[:-4]  # All but the last 5 characters (score)
                method = score_with_method[-4:]  # Last 5 characters (method)
                
                # Write the formatted line to the output file, adding a space between score and method
                out_file.write(f"{facet_id} {query_id} {doc_id} {rank} {score} {method.strip()}\n")

print(f"Converted .run file written to {output_file}")

Converted .run file written to ./first_turn/test_first_turn.run


In [78]:
import json

# File paths
file1 = "./first_turn/test_dataset_bert_first_turn_poop.json"  # First JSON file
file2 = "./first_turn/train_dataset_bert_first_turn.json"  # Second JSON file
output_file = "./first_turn/train_test_dataset_bert_first_turn_poop.json"  # Output file

# Read and load the JSON files
with open(file1, "r") as f1, open(file2, "r") as f2:
    data1 = json.load(f1)  # Load the first JSON file
    data2 = json.load(f2)  # Load the second JSON file

# Combine the two lists
combined_data = data1 + data2  # Concatenate lists

# Write the combined data to a new JSON file
with open(output_file, "w") as out:
    json.dump(combined_data, out, indent=4)  # Save with pretty formatting

print(f"Combined JSON saved to {output_file}")

Combined JSON saved to ./first_turn/train_test_dataset_bert_first_turn_poop.json
